In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

# Для работы с матрицами
from scipy.sparse import csr_matrix, coo_matrix

# Детерминированные алгоритмы
from implicit.nearest_neighbours import ItemItemRecommender, CosineRecommender, TFIDFRecommender, BM25Recommender

# Метрики
from implicit.evaluation import train_test_split
from implicit.evaluation import precision_at_k, mean_average_precision_at_k, AUC_at_k, ndcg_at_k

In [2]:
data = pd.read_csv('retail_train.csv')
data.head(2)

user_id    basket_id  day  item_id  quantity  sales_value  store_id  \
0     2375  26984851472    1  1004906         1         1.39       364   
1     2375  26984851472    1  1033142         1         0.82       364   

   retail_disc  trans_time  week_no  coupon_disc  coupon_match_disc  
0         -0.6        1631        1          0.0                0.0  
1          0.0        1631        1          0.0                0.0

In [3]:
test_size_weeks = 3

data_train = data[data['week_no'] < data['week_no'].max() - test_size_weeks]
data_test = data[data['week_no'] >= data['week_no'].max() - test_size_weeks]

# Оценивание
За выполнени каждого задания 1 балл

4 балла -> отл

3 балла -> хор

И тд

### Задание 0. Товар 999999
На вебинаре мы использовали товар 999999 - что это за товар?

Товары, которые покупали меньше всего(не популярные товары) - товары которые не попали в ТОП 5000

Зачем он нужен?

Для того, чтобы мы не потряли пользователей, которые покупали такой товар

Используя этот товар мы смещаем качество рекомендаций.В какую сторону?

Скорее всего он будет ухудшать качество рекомендаций. Потому что ограничен числом покупателей

Можно ли удалить этот товар?   

Товар удалить нельзя, мы рискуем потерять некоторый сегмент покупателей, заинтересованных в нем.
Уберите этот товар и сравните с качеством на семинаре.

In [4]:
popularity = data_train.groupby('item_id')['quantity'].sum().reset_index()
popularity.rename(columns={'quantity': 'n_sold'}, inplace=True)

popularity.head()

item_id  n_sold
0    25671       6
1    26081       1
2    26093       1
3    26190       1
4    26355       2

In [5]:
top_5000 = popularity.sort_values('n_sold', ascending=False).head(5000).item_id.tolist()
top_5000

[6534178,
 6533889,
 6534166,
 6544236,
 1404121,
 397896,
 1426702,
 5703832,
 480014,
 5668996,
 6410462,
 420647,
 5747420,
 731106,
 5716076,
 707683,
 202291,
 1153346,
 1082185,
 5747233,
 6410464,
 545926,
 995242,
 2848087,
 1388206,
 1029743,
 5712216,
 5850988,
 1133018,
 1106523,
 1007195,
 981760,
 5845857,
 883404,
 1127831,
 2690723,
 866227,
 995785,
 860776,
 951590,
 5569230,
 908531,
 916122,
 826249,
 1098066,
 862349,
 1058997,
 1044078,
 904360,
 840361,
 923746,
 1126899,
 849843,
 961554,
 1005186,
 820165,
 1053690,
 844179,
 844165,
 1070820,
 1065593,
 834484,
 994928,
 833715,
 859075,
 1022003,
 1013321,
 938700,
 854852,
 986947,
 5569471,
 927191,
 1071939,
 1096036,
 1004906,
 986912,
 1080414,
 914190,
 908846,
 962229,
 8090521,
 1085604,
 911878,
 1092026,
 866211,
 1068719,
 878996,
 8090537,
 1081177,
 847270,
 929668,
 1024306,
 909894,
 907014,
 903325,
 910032,
 1095275,
 833025,
 862139,
 962568,
 953476,
 847982,
 999971,
 968215,
 1028816,
 976

In [6]:
# не будем заводить фиктивный item_id (если юзер НЕ покупал товары из топ-5000, то он "купил" такой товар)
#data_train.loc[~data_train['item_id'].isin(top_5000), 'item_id'] = 999999

user_item_matrix = pd.pivot_table(data_train, 
                                  index='user_id', columns='item_id', 
                                  values='quantity',
                                  aggfunc='count', 
                                  fill_value=0
                                 )

user_item_matrix[user_item_matrix > 0] = 1 # так как в итоге хотим предсказать 
user_item_matrix = user_item_matrix.astype(float) # необходимый тип матрицы для implicit

# переведем в формат saprse matrix
sparse_user_item = csr_matrix(user_item_matrix).tocsr()

user_item_matrix.head(3)

item_id  25671     26081     26093     26190     26355     26426     26540     \
user_id                                                                         
1             0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2             0.0       0.0       0.0       0.0       0.0       0.0       0.0   
3             0.0       0.0       0.0       0.0       0.0       0.0       0.0   

item_id  26601     26636     26691     ...  17328742  17329473  17329749  \
user_id                                ...                                 
1             0.0       0.0       0.0  ...       0.0       0.0       0.0   
2             0.0       0.0       0.0  ...       0.0       0.0       0.0   
3             0.0       0.0       0.0  ...       0.0       0.0       0.0   

item_id  17330255  17330511  17381856  17382205  17383227  17827644  17829232  
user_id                                                                        
1             0.0       0.0       0.0       0.0       0.0       0.0       0.0  
2             0.0       0.0       0.0       0.0       0.0       0.0       0.0  
3             0.0       0.0       0.0       0.0       0.0       0.0       0.0  

[3 rows x 86865 columns]

In [7]:
user_item_matrix.sum().sum() / (user_item_matrix.shape[0] * user_item_matrix.shape[1]) * 100

0.5804511409122447

Возможно я что-то не поняла, но количество заполненых ячеек стало гораздо меньше, чем когла мы ввели товар 999999

In [8]:
userids = user_item_matrix.index.values
itemids = user_item_matrix.columns.values

matrix_userids = np.arange(len(userids))
matrix_itemids = np.arange(len(itemids))

id_to_itemid = dict(zip(matrix_itemids, itemids))
id_to_userid = dict(zip(matrix_userids, userids))

itemid_to_id = dict(zip(itemids, matrix_itemids))
userid_to_id = dict(zip(userids, matrix_userids))

In [10]:
? ItemItemRecommender

In [10]:
%%time

model = ItemItemRecommender(K=5, num_threads=4) # K - кол-во билжайших соседей

model.fit(csr_matrix(user_item_matrix).T.tocsr(),  # На вход item-user matrix
          show_progress=True)

recs = model.recommend(userid=userid_to_id[2],  # userid - id от 0 до N
                        user_items=csr_matrix(user_item_matrix).tocsr(),   # на вход user-item matrix
                        N=5, # кол-во рекомендаций 
                        filter_already_liked_items=False, 
                        filter_items=None, 
                        recalculate_user=True)

NameError: name 'userid_to_id' is not defined

In [9]:
[id_to_itemid[rec[0]] for rec in recs]

NameError: name 'recs' is not defined

### Задание 1. Weighted Random Recommendation

Напишите код для случайных рекоммендаций, в которых вероятность рекомендовать товар прямо пропорциональна логарифму продаж
- Можно сэмплировать товары случайно, но пропорционально какому-либо весу
- Например, прямопропорционально популярности. вес = log(sales_sum товара)
- Придумайте пример 3 весов, посчитайте weighted_random_recommendation для разных весов

In [49]:
def weighted_random_recommendation(items_weights, n=5):
    items_weights = data_train.groupby(by='item_id')['sales_value'].sum().reset_index().rename(columns={'sales_value':'weight'})
    items = np.array(items_weights['item_id'])
    recs = np.random.choice(items, size=n, replace=False)
    return recs.tolist()

In [50]:
result = data_test.groupby('user_id')['item_id'].unique().reset_index()
result.columns=['user_id', 'actual']

In [51]:
%%time
result['weighted_random_recommendation'] = result['user_id'].apply(lambda x: weighted_random_recommendation(items_weights, n=5))

Wall time: 6min 44s


In [88]:
result.head(3)

user_id                                             actual  \
0        1  [821867, 834484, 856942, 865456, 889248, 90795...   
1        3  [835476, 851057, 872021, 878302, 879948, 90963...   
2        6  [920308, 926804, 946489, 1006718, 1017061, 107...   

                  weighted_random_recommendation  
0   [9935500, 94207, 13872188, 907441, 13777278]  
1  [15488637, 929396, 5567574, 1081984, 1095318]  
2   [8069383, 1887925, 9297223, 820923, 1030879]

### Задание 2. Расчет метрик
Рассчитайте Precision@5 для каждого алгоритма (с вебинара и weighted_random_recommendation) с помощью функции из вебинара 1. Какой алгоритм показывает лучшее качество? Почему?

In [89]:
data_res = pd.read_csv('predictions_basic.csv')
data_res.head(2)

user_id                                             actual  \
0        1  [821867, 834484, 856942, 865456, 889248, 90795...   
1        3  [835476, 851057, 872021, 878302, 879948, 90963...   

                            random_recommendation  \
0  [1112627, 1090336, 12172054, 6760457, 5570409]   
1    [9803371, 1139418, 2580088, 926777, 1098786]   

                          popular_recommendation  \
0  [6534178, 6533889, 1029743, 6534166, 1082185]   
1  [6534178, 6533889, 1029743, 6534166, 1082185]   

                                     itemitem  \
0  [999999, 1082185, 981760, 1127831, 995242]   
1  [999999, 1082185, 981760, 1098066, 995242]   

                                        cosine  \
0  [1082185, 999999, 981760, 1127831, 1098066]   
1   [1082185, 1098066, 981760, 999999, 826249]   

                                         tfidf  \
0  [1082185, 981760, 1127831, 999999, 1098066]   
1   [1082185, 981760, 1098066, 826249, 999999]   

                                  own_purchases  
0   [999999, 1082185, 1029743, 995785, 1004906]  
1  [999999, 1082185, 1098066, 6534178, 1127831]

In [90]:
def precision_at_k(recommended_list, bought_list, k=5):
    
    bought_list = np.array(bought_list)
    print(bought_list)
    recommended_list = np.array(recommended_list)
    
    bought_list = bought_list  # Тут нет [:k] !!
    recommended_list = recommended_list[:k]
    
    flags = np.isin(bought_list, recommended_list)
    
    precision = flags.sum() / len(recommended_list)
    
    
    return precision

In [67]:
?map

In [78]:
data_res['actual'].map(lambda x: x[1:-1].split(', ')).apply(lambda x: list(map(int, x)))[0]

[821867,
 834484,
 856942,
 865456,
 889248,
 907957,
 914190,
 943316,
 951954,
 954486,
 958046,
 962568,
 969231,
 971585,
 979707,
 986947,
 990656,
 995242,
 1004906,
 1005186,
 1042083,
 1050310,
 1060819,
 1062002,
 1064441,
 1069733,
 1074612,
 1082185,
 1131115,
 1132771,
 6534544,
 13876341,
 15971874,
 17178953,
 883616,
 917704,
 931860,
 961554,
 1002032,
 1031190,
 8090541,
 8293439,
 9297615,
 9527329,
 15926712,
 1049998,
 861272,
 869465,
 877373,
 908213,
 933913,
 940947,
 945809,
 959316,
 978974,
 1031697,
 1041796,
 1048918,
 1081189,
 1101422,
 1115576,
 1122428,
 1132231,
 1132814,
 5577022,
 8091601,
 9296986,
 9677939,
 10356149,
 13417048,
 15741823,
 15830875]

In [91]:
result_1 = result.copy()

In [92]:
result_1.drop(['actual'], axis='columns', inplace=True)

In [96]:
result_new = pd.merge(data_res, result, how ='inner', on ='user_id')
result_new.head(2)

user_id                                           actual_x  \
0        1  [821867, 834484, 856942, 865456, 889248, 90795...   
1        3  [835476, 851057, 872021, 878302, 879948, 90963...   

                            random_recommendation  \
0  [1112627, 1090336, 12172054, 6760457, 5570409]   
1    [9803371, 1139418, 2580088, 926777, 1098786]   

                          popular_recommendation  \
0  [6534178, 6533889, 1029743, 6534166, 1082185]   
1  [6534178, 6533889, 1029743, 6534166, 1082185]   

                                     itemitem  \
0  [999999, 1082185, 981760, 1127831, 995242]   
1  [999999, 1082185, 981760, 1098066, 995242]   

                                        cosine  \
0  [1082185, 999999, 981760, 1127831, 1098066]   
1   [1082185, 1098066, 981760, 999999, 826249]   

                                         tfidf  \
0  [1082185, 981760, 1127831, 999999, 1098066]   
1   [1082185, 981760, 1098066, 826249, 999999]   

                                  own_purchases  \
0   [999999, 1082185, 1029743, 995785, 1004906]   
1  [999999, 1082185, 1098066, 6534178, 1127831]   

                                            actual_y  \
0  [821867, 834484, 856942, 865456, 889248, 90795...   
1  [835476, 851057, 872021, 878302, 879948, 90963...   

                  weighted_random_recommendation  
0   [9935500, 94207, 13872188, 907441, 13777278]  
1  [15488637, 929396, 5567574, 1081984, 1095318]

In [97]:
result_new['actual_x'] = result_new['actual_x'].map(lambda x: x[1:-1].split(', ')).apply(lambda x: list(map(int, x)))
presision = pd.DataFrame(index=['precision'])

for i in result_new.columns[2:]:
    if i != 'weighted_random_recommendation':
        result_new[i] = result_new[i].map(lambda x: x[1:-1].split(', ')).apply(lambda x: list(map(int, x)))
    res = result_new.apply(lambda x: precision_at_k(x[i], x['actual_x'],  5), axis=1)
    presision[i] = res.mean();

[  821867   834484   856942   865456   889248   907957   914190   943316
   951954   954486   958046   962568   969231   971585   979707   986947
   990656   995242  1004906  1005186  1042083  1050310  1060819  1062002
  1064441  1069733  1074612  1082185  1131115  1132771  6534544 13876341
 15971874 17178953   883616   917704   931860   961554  1002032  1031190
  8090541  8293439  9297615  9527329 15926712  1049998   861272   869465
   877373   908213   933913   940947   945809   959316   978974  1031697
  1041796  1048918  1081189  1101422  1115576  1122428  1132231  1132814
  5577022  8091601  9296986  9677939 10356149 13417048 15741823 15830875]
[  835476   851057   872021   878302   879948   909638   913202   920626
   958154   994891  1053690  1083328  1096727  6463658  7167218  7167249
  9526563  9526886 13842214]
[  920308   926804   946489  1006718  1017061  1078346  1104227  1108624
  1110392  1120741 13776852 17105539   825541   870315   873654   874149
   956672  1071939  5

   875502   901772   931015]
[ 6534178   826249   849470   858743   916758   935968  1010578  1075175
  1119830  1120362  5568489  5569845  5978656 13158992 13945244 14050714
   840173   860362   884120  1075505  1137540  7441679 16769972   825749
   840102   841220   858439   869874   880150   897270   904360   906763
   912457   912704   932182   944836   947220   956373   962161   977033
   995965  1018339  1059473  1070820  1082185  1117358  1130177  6039994
  8144652 13115981 15506577 15511891 15925349   898494   927191   976199
  1009567  1023473  1025641  1073775  1104604  1120511  8119297 12756877
   827656   903674   930602   943286   991874   995645  1001702  1011259
  1047619  1051110  1057124  1071733  1075074  1087660  1092160  5569374
  6464020  7410013 13876403]
[ 1034176  9487286   851819   969568  1032297  1097018 13034781   849202
  1075368]
[  831815   844165   849843   853904   903230  1011832  1022003  1036501
  1050229  1056762  1061971  1068719  1092026  1096036 

 12731466 15596145 15687070]
[ 820165  859924  865511 1055504 1075175 1130893  876042  901397 7410217]
[  857000   890533   960718   971585   979178   996064  1040700  1131550
 15597118 16219167   835482   850990   867460   879564  1003257  1022119
  1028890  7410335  9445777 10285335 13095319 15736860   831628   839454
   841905   855916   868423   880150   897954   913144   934639   944376
  1040346  1080841  9485437  9487498  9835509 13944709 15596180 15596488
 15972228]
[  831808   840732   846202   873782   893501   900770   911311   936741
   990256  1011427  1014915  1028715  1051882  1054402  1070820  1074333
  1086061  1101771  1107420  1115228  1125391  1129610  1139569  5569471
  8156489 13134075   823704   879049   967994   969980   904236  6632909
   834631   839243   841236   862732   874617   899201   922381   924786
   932242   940108   949645   981760   982960   987941   999134  1042907
  1053530  1078346  1082185  1096851  1104056  1115175  1123842  1126899
 10121646 

 15506577]
[ 1055863  1068719   879755  9526886 12605952 15971801   917826  1029743
  1039348  1082185  1082990   981877   840361   845705   866778   883404
   884774   899624   919157   933835   947798   977798  1050968  1062782
  1065593  1104146  6904459   947865  1085604   833723  9527158  7168026
   830887   831509   844179   890610   951590  1040807  1082544  1106523
  6463937  1013928  6534178   963336   949965  1004906  1086641  1110244
  9245106   885697   995242  9526563   856772   866140   913785   923746
   927191   934676   938700   986760   999134  1013321  1038746  1047349
  1075470  1092945  1101010  1118033  1133827  1138125   819063   899473
   981760   999858]
[  918733  1084208   824180   824555   835973   837751   840011   845163
   859075   885290   891217   891648   892221   892294   897306   899624
   905286   906335   912902   913785   923849   923967   925862   928049
   941033   943076   951526   951590   952563   960791   963228   965766
   969205   972143  

 12693102 13416299 13909962 13910730]
[  878910   956995  1055863  9879409 12781501]
[ 840890  856519  862535  880438  914077  942299  947312  951761  955012
  986912 1008546 1018780 1035600 1069899 1078652 1082185 1088775 1135552
 6424464]
[ 6534178  7433029   859075  1082185 14106445   838637   854483   913785
   989275  1029743  1043128  1056746  9831557   962343  1000148 13007507
   910964  1024833  1075637  1126528  1128955  1134732 10285073   873203
   896923   972342  1022097  9446520   968882  1046339  1109014   940804
   990814]
[  824005   932503  1001675 10285141 15630134   845208   848071   869177
   899624   962568   995785   996114  1008316  1037863  1055646  1126746
  6552318  9547021 13133557  1049822  1051288  1058997  1070702  1096643
  1113111  6396566  6424447]
[  994953  1108689 12604267]
[ 6443200  6443261  6534178   919157  1029743  1084997  6391426  9879409
 15972415   835236   855716   881788   908846   986382   987494   998444
  1051741  1082185  1098248 17104

...

  7168026  8019977  9242395 12262978 13158500 15568874 17902077]
[  819927   822407   832678   836393   844179   847241   860167   874061
   878880   880253   887003   893739   913210   930917   933569   938547
   951590   951703   964968   968214   972931   974340   995502  1000707
  1002934  1022003  1029513  1030040  1039224  1043751  1046968  1056651
  1060363  1067820  1070898  1080841  1082185  1089954  1108296  1120559
  1130858  1134810  8090521  9655482 12810393 13007411 15716664 15717285
 15926885 15927932 16055892  1037840  6534178]
[  821845   828143   880290   911812   914190   920367   945998   962782
   977791   981760  1029743  1060476  1062117  1093331  1134174  1137483
  9245467 10285133   834484   855434   933794  1043563  1111684 17105729
   847982   855279   901509   908531   916993   922896   936830   992292
  1014054  1024643  1038217  1069312  1135447  5566472  6034857  8249120
  9705473  9827950   900175]
[ 6533889   918676  1029743  1085161 10457471   929751  

  1009977  7025106  9420043 12582253 13511447]
[ 6534178   827570   831712   835616   836983   843744   865456   877358
   909306   911470   976199   982985   999581  1031483  1052549  1060408
  1068258  1070463  1075637  1082947  1095645  1110126  5995046  6979222
  7025106  7441198  9574160  9677543  9856740  9881593 10344971 12525256
 15452338 15452726 15863619 16223273 17178953   922092  1004001  1026162
  5978656 15973205   819967   862349   867058   884686   909086   927299
   959219   968164   970030  1026118  1054123  1079878  1082185  1096317
  1117473  1135476  5578547  5585639  8293440  9881592 13871141 15717261]
[  834484   837569   854754   888186   890999   943911  1023226  1024306
  1082185  1097458  5563693  1029743   835796   878996   894414   948953
  1051516  1110142  7025125 12757087 12949378 13654702   827218   840694
   880150   887350   900802   901397   902167   907099   917033   918687
   925029   948670   949965   952254   959219   971165   971314   976300
   

  5587133  5588666  8011397 15716403]
[  988572  1029112  1082185  1096792   838981   865330   967395  1031316
  9831489 12810645   847982   901062   934369  1014802  1106523   866227
   976998  1062966  1133018  5568228  9571047]
[  820291   832513   841035   857827   997689   839094   844165   862349
   868764   874820   883932   916122   962671   989194   996333   999858
  1033046  1071939  8290587   880969   893018   989824  1005493  1098066
  9707240 12301338 15506577]
[  821083   858160   959076   979707  1025650 15926844]
[851819 895680 969568 979975 995628]
[  822238   854852   865668   910255   920844   930118   968215   970030
   991575  1029743  1076881  1091993  1136715  5585331  6034964  7442317
 12263024 12757316 15972491   837167   844165   869477   884244   927379
   930678   967692  1101052  1126400  6979089  9296804  9526360  9527027
  9527128  9574145 13213683 13417584 15595917 15973056   970792  1026118
  1032967  1068292 10311401 10456602 15596140 15596923]
[ 82016

  1110695  1119879  1122568  5568729 12330794 13073103 13133787 15596275]
[ 1074271  1129576   849843  1055646  1056651   847270   847789   894627
   948832   959830  1044299  1071697  1089392 13115894]
[  828331   834117   835476   855488   862981   863259   888054   888476
   893867   900842   923746   937292   944139   947292   953476   957089
   999198  1005186  1008220  1010029  1017813  1022340  1023226  1039927
  1061201  1070272  1077281  1084613  1086806  1095751  1096036  1106523
  5569172  5591083  9487467  9803483 12648967 12670071 15831147 15926775
   883404   912004   976864  1003188  1011736  1024132  1028890  1053690
  1075793  5568789  9858794 10285335 12384775 12987835 15506577 15716783
 15831241 15926887 16221105 12582494]
[  859075  1053598  1071939  5568729  9553191 13512383]
[1096603]
[6534178]
[ 1016709  9835695  1132298 16809501   845294   871756   873654  1023226
  1068719  1078912  1115187  1127338  1134222  1135834  5569230  6961763
  6979579  7025204  744167

AttributeError: 'numpy.ndarray' object has no attribute 'split'

In [98]:
presision

random_recommendation  popular_recommendation  itemitem    cosine  \
precision                0.00049                 0.15524  0.136925  0.132909   

              tfidf  own_purchases  
precision  0.138981       0.179693

### Задание 3. Улучшение бейзлайнов и ItemItem

- Попробуйте улучшить бейзлайны, считая их на топ-5000 товаров
- Попробуйте улучшить разные варианты ItemItemRecommender, выбирая число соседей $K$.
- Попробуйте стратегии ансамблирования изученных алгоритмов


In [99]:
def random_recommendation(items, n=5):
    """Случайные рекоммендации"""
    
    
    items = np.array(items)
    recs = np.random.choice(items, size=n, replace=False)
    
    return recs.tolist()

In [100]:
popularity = data_train.groupby('item_id')['quantity'].sum().reset_index()
popularity.rename(columns={'quantity': 'n_sold'}, inplace=True)
items = popularity.sort_values('n_sold', ascending=False).head(5000).item_id.tolist()

result_new['r_5000'] = result_new['user_id'].apply(lambda x: random_recommendation(items, n=5))

In [108]:
res = result_new.apply(lambda x: precision_at_k(x['r_5000'], x['actual_x'],  5), axis=1)
presision['r_5000'] = res.mean();

[  821867   834484   856942   865456   889248   907957   914190   943316
   951954   954486   958046   962568   969231   971585   979707   986947
   990656   995242  1004906  1005186  1042083  1050310  1060819  1062002
  1064441  1069733  1074612  1082185  1131115  1132771  6534544 13876341
 15971874 17178953   883616   917704   931860   961554  1002032  1031190
  8090541  8293439  9297615  9527329 15926712  1049998   861272   869465
   877373   908213   933913   940947   945809   959316   978974  1031697
  1041796  1048918  1081189  1101422  1115576  1122428  1132231  1132814
  5577022  8091601  9296986  9677939 10356149 13417048 15741823 15830875]
[  835476   851057   872021   878302   879948   909638   913202   920626
   958154   994891  1053690  1083328  1096727  6463658  7167218  7167249
  9526563  9526886 13842214]
[  920308   926804   946489  1006718  1017061  1078346  1104227  1108624
  1110392  1120741 13776852 17105539   825541   870315   873654   874149
   956672  1071939  5

   875502   901772   931015]
[ 6534178   826249   849470   858743   916758   935968  1010578  1075175
  1119830  1120362  5568489  5569845  5978656 13158992 13945244 14050714
   840173   860362   884120  1075505  1137540  7441679 16769972   825749
   840102   841220   858439   869874   880150   897270   904360   906763
   912457   912704   932182   944836   947220   956373   962161   977033
   995965  1018339  1059473  1070820  1082185  1117358  1130177  6039994
  8144652 13115981 15506577 15511891 15925349   898494   927191   976199
  1009567  1023473  1025641  1073775  1104604  1120511  8119297 12756877
   827656   903674   930602   943286   991874   995645  1001702  1011259
  1047619  1051110  1057124  1071733  1075074  1087660  1092160  5569374
  6464020  7410013 13876403]
[ 1034176  9487286   851819   969568  1032297  1097018 13034781   849202
  1075368]
[  831815   844165   849843   853904   903230  1011832  1022003  1036501
  1050229  1056762  1061971  1068719  1092026  1096036 

 12731466 15596145 15687070]
[ 820165  859924  865511 1055504 1075175 1130893  876042  901397 7410217]
[  857000   890533   960718   971585   979178   996064  1040700  1131550
 15597118 16219167   835482   850990   867460   879564  1003257  1022119
  1028890  7410335  9445777 10285335 13095319 15736860   831628   839454
   841905   855916   868423   880150   897954   913144   934639   944376
  1040346  1080841  9485437  9487498  9835509 13944709 15596180 15596488
 15972228]
[  831808   840732   846202   873782   893501   900770   911311   936741
   990256  1011427  1014915  1028715  1051882  1054402  1070820  1074333
  1086061  1101771  1107420  1115228  1125391  1129610  1139569  5569471
  8156489 13134075   823704   879049   967994   969980   904236  6632909
   834631   839243   841236   862732   874617   899201   922381   924786
   932242   940108   949645   981760   982960   987941   999134  1042907
  1053530  1078346  1082185  1096851  1104056  1115175  1123842  1126899
 10121646 

 15506577]
[ 1055863  1068719   879755  9526886 12605952 15971801   917826  1029743
  1039348  1082185  1082990   981877   840361   845705   866778   883404
   884774   899624   919157   933835   947798   977798  1050968  1062782
  1065593  1104146  6904459   947865  1085604   833723  9527158  7168026
   830887   831509   844179   890610   951590  1040807  1082544  1106523
  6463937  1013928  6534178   963336   949965  1004906  1086641  1110244
  9245106   885697   995242  9526563   856772   866140   913785   923746
   927191   934676   938700   986760   999134  1013321  1038746  1047349
  1075470  1092945  1101010  1118033  1133827  1138125   819063   899473
   981760   999858]
[  918733  1084208   824180   824555   835973   837751   840011   845163
   859075   885290   891217   891648   892221   892294   897306   899624
   905286   906335   912902   913785   923849   923967   925862   928049
   941033   943076   951526   951590   952563   960791   963228   965766
   969205   972143  

 12693102 13416299 13909962 13910730]
[  878910   956995  1055863  9879409 12781501]
[ 840890  856519  862535  880438  914077  942299  947312  951761  955012
  986912 1008546 1018780 1035600 1069899 1078652 1082185 1088775 1135552
 6424464]
[ 6534178  7433029   859075  1082185 14106445   838637   854483   913785
   989275  1029743  1043128  1056746  9831557   962343  1000148 13007507
   910964  1024833  1075637  1126528  1128955  1134732 10285073   873203
   896923   972342  1022097  9446520   968882  1046339  1109014   940804
   990814]
[  824005   932503  1001675 10285141 15630134   845208   848071   869177
   899624   962568   995785   996114  1008316  1037863  1055646  1126746
  6552318  9547021 13133557  1049822  1051288  1058997  1070702  1096643
  1113111  6396566  6424447]
[  994953  1108689 12604267]
[ 6443200  6443261  6534178   919157  1029743  1084997  6391426  9879409
 15972415   835236   855716   881788   908846   986382   987494   998444
  1051741  1082185  1098248 17104

...

  9836434 10312139  1110572  5589005  8090513 16809581]
[  821741   837751   868147   883404   921836   940023  1029743  1037631
  1043494  1044599  1066289  1082185  1082212  1127470  5568378  5568732
  5568845  5570595  6602697  8118618 15452729 15511891 15596568 15926712
 15926725 15926962   847260   873447   922737   937688   962568  1008626
  1025545  1031697  1078224  1103004  5570109  6904666 13876497  6463717
  8090532  8090545  8090610  8175880 15716085 15716597 15716608 17214937
 17215029  6533765  6534178   823721   824005   850044   853262   859427
   918018   931608   936914   949991   955587   972143   981760   991303
   995242  1005274  1048462  1048472  1049897  1071757  1091383  1103556
  1108854  5566472  5581203  7168463  9242345 15926911   860776   987122
  6514190 13416932   834826   859075  1124551  1131529]
[ 1022003  1050229 12525233 15801304 17329749   914077   923746  1001953
  1048272  1050530  1120349  1126899 13512060 13877192   844165   874061
   910109   

  7168026  8019977  9242395 12262978 13158500 15568874 17902077]
[  819927   822407   832678   836393   844179   847241   860167   874061
   878880   880253   887003   893739   913210   930917   933569   938547
   951590   951703   964968   968214   972931   974340   995502  1000707
  1002934  1022003  1029513  1030040  1039224  1043751  1046968  1056651
  1060363  1067820  1070898  1080841  1082185  1089954  1108296  1120559
  1130858  1134810  8090521  9655482 12810393 13007411 15716664 15717285
 15926885 15927932 16055892  1037840  6534178]
[  821845   828143   880290   911812   914190   920367   945998   962782
   977791   981760  1029743  1060476  1062117  1093331  1134174  1137483
  9245467 10285133   834484   855434   933794  1043563  1111684 17105729
   847982   855279   901509   908531   916993   922896   936830   992292
  1014054  1024643  1038217  1069312  1135447  5566472  6034857  8249120
  9705473  9827950   900175]
[ 6533889   918676  1029743  1085161 10457471   929751  

  1009977  7025106  9420043 12582253 13511447]
[ 6534178   827570   831712   835616   836983   843744   865456   877358
   909306   911470   976199   982985   999581  1031483  1052549  1060408
  1068258  1070463  1075637  1082947  1095645  1110126  5995046  6979222
  7025106  7441198  9574160  9677543  9856740  9881593 10344971 12525256
 15452338 15452726 15863619 16223273 17178953   922092  1004001  1026162
  5978656 15973205   819967   862349   867058   884686   909086   927299
   959219   968164   970030  1026118  1054123  1079878  1082185  1096317
  1117473  1135476  5578547  5585639  8293440  9881592 13871141 15717261]
[  834484   837569   854754   888186   890999   943911  1023226  1024306
  1082185  1097458  5563693  1029743   835796   878996   894414   948953
  1051516  1110142  7025125 12757087 12949378 13654702   827218   840694
   880150   887350   900802   901397   902167   907099   917033   918687
   925029   948670   949965   952254   959219   971165   971314   976300
   

  5587133  5588666  8011397 15716403]
[  988572  1029112  1082185  1096792   838981   865330   967395  1031316
  9831489 12810645   847982   901062   934369  1014802  1106523   866227
   976998  1062966  1133018  5568228  9571047]
[  820291   832513   841035   857827   997689   839094   844165   862349
   868764   874820   883932   916122   962671   989194   996333   999858
  1033046  1071939  8290587   880969   893018   989824  1005493  1098066
  9707240 12301338 15506577]
[  821083   858160   959076   979707  1025650 15926844]
[851819 895680 969568 979975 995628]
[  822238   854852   865668   910255   920844   930118   968215   970030
   991575  1029743  1076881  1091993  1136715  5585331  6034964  7442317
 12263024 12757316 15972491   837167   844165   869477   884244   927379
   930678   967692  1101052  1126400  6979089  9296804  9526360  9527027
  9527128  9574145 13213683 13417584 15595917 15973056   970792  1026118
  1032967  1068292 10311401 10456602 15596140 15596923]
[ 82016

  1110695  1119879  1122568  5568729 12330794 13073103 13133787 15596275]
[ 1074271  1129576   849843  1055646  1056651   847270   847789   894627
   948832   959830  1044299  1071697  1089392 13115894]
[  828331   834117   835476   855488   862981   863259   888054   888476
   893867   900842   923746   937292   944139   947292   953476   957089
   999198  1005186  1008220  1010029  1017813  1022340  1023226  1039927
  1061201  1070272  1077281  1084613  1086806  1095751  1096036  1106523
  5569172  5591083  9487467  9803483 12648967 12670071 15831147 15926775
   883404   912004   976864  1003188  1011736  1024132  1028890  1053690
  1075793  5568789  9858794 10285335 12384775 12987835 15506577 15716783
 15831241 15926887 16221105 12582494]
[  859075  1053598  1071939  5568729  9553191 13512383]
[1096603]
[6534178]
[ 1016709  9835695  1132298 16809501   845294   871756   873654  1023226
  1068719  1078912  1115187  1127338  1134222  1135834  5569230  6961763
  6979579  7025204  744167

In [109]:
presision[['random_recommendation','r_5000']]

random_recommendation    r_5000
precision                0.00049  0.006856

### Задание 4. Улучшение детерминированных алгоритмов
На семинаре мы рассматривали 



Далее $U \equiv N_i(u) $

$$r_{u,i} =  \frac{1}{S}\sum\limits_{v \in U}\operatorname{sim}(u,v)r_{v, i}$$
$$ S = \sum\limits_{v \in U} \operatorname{sim}(u,v)$$

Предлагается улучшить эту формулу и учесть средние предпочтения всех пользователей

$$r_{u,i} = \mu + \bar{r_u} + \frac{1}{S}\sum\limits_{v \in U}\operatorname{sim}(u,v)(r_{v, i}-\bar{r_{v}} - \mu)$$

Какие смысл имееют $ \mu $ и $ \bar{r_u}$ ?

Реализуйте алгоритм, прогнозирующий рейтинги на основе данной формулы, на numpy (векторизованно!)

В качестве схожести возьмите CosineSimilarity.

Примените к user_item_matrix. В качестве рейтингов возьмите количество или стоимость купленного товара. 
Данный алгоритм предсказывает рейтинги. Как на основании предсказанных рейтингов предсказать факт покупки?

Предложите вариант.
Посчитайте accuracy@5 и сравните с алгоритмами, разобранными на вебинаре.

In [1]:
conda install -c conda-forge implicit

Solving environment: ...working... failed with initial frozen solve. Retrying with flexible solve.
Solving environment: ...working... failed with repodata from current_repodata.json, will retry with next repodata source.
Solving environment: ...working... done

## Package Plan ##

  environment location: C:\Users\User\Anaconda3

  added / updated specs:
    - implicit


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2019.9.11          |           py37_0         147 KB  conda-forge
    conda-4.9.2                |   py37h03978a9_0         3.0 MB  conda-forge
    implicit-0.4.2             |   py37h9b59f54_1         496 KB  conda-forge
    python_abi-3.7             |          1_cp37m           4 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.7 MB

The following NEW packages will be INSTA



==> WARNING: A newer version of conda exists. <==
  current version: 4.7.12
  latest version: 4.9.2

Please update conda by running

    $ conda update -n base -c defaults conda




In [2]:
conda update -n base -c defaults conda

Solving environment: ...working... done

## Package Plan ##

  environment location: C:\Users\User\Anaconda3

  added / updated specs:
    - conda


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    backports.functools_lru_cache-1.6.1|     pyhd3eb1b0_0          12 KB
    backports.tempfile-1.0     |     pyhd3eb1b0_1          11 KB
    conda-4.9.2                |   py37haa95532_0         2.9 MB
    conda-package-handling-1.7.2|   py37h76e460a_0         724 KB
    future-0.18.2              |           py37_1         646 KB
    ------------------------------------------------------------
                                           Total:         4.2 MB

The following packages will be UPDATED:

  backports.functoo~                               1.5-py_2 --> 1.6.1-pyhd3eb1b0_0
  conda-package-han~                   1.6.0-py37h62dcd97_0 --> 1.7.2-py37h76e460a_0
  future                         